# Import Libraries

In [1]:
from gurobipy import *
import pandas as pd
%matplotlib inline
import matplotlib as mpl
import matplotlib.pyplot as plt
import pysd
import pandas as pd
import numpy as np
import geopandas as gp
import zipfile
import requests
import networkx as nx
import matplotlib.cm
import math
from math import radians, sin, cos, acos
from geopy.distance import geodesic
import requests
from bs4 import BeautifulSoup
from osgeo import ogr, osr
import matplotlib.cm as cmx
import matplotlib.colors as colors
from Circles.circles import circle
from shapely.geometry import Polygon, Point
from descartes import PolygonPatch
from shapely.ops import cascaded_union
import pickle
from mpl_toolkits.basemap import Basemap
from matplotlib.patches import Polygon
from matplotlib.collections import PatchCollection
from matplotlib.colors import Normalize
import datacompy
import warnings
warnings.filterwarnings("ignore")
import time

# Import Input Data (Model Parameters)

In [2]:
with open('Case1DataParameters', 'rb') as fp:
    mhi = pickle.load(fp)
    chi = pickle.load(fp)
    Qi = pickle.load(fp)
    uio = pickle.load(fp)
    cio = pickle.load(fp)
    capi = pickle.load(fp)
    xiiinit = pickle.load(fp)
    B = pickle.load(fp)
    Pi = pickle.load(fp)
    Tcost = pickle.load(fp)

with open('Case1compDPs', 'rb') as fp:
    compDPslist = pickle.load(fp)
    compviablelist = pickle.load(fp)

with open('Case1Fijlist', 'rb') as fp:
    compFijlist = pickle.load(fp)

with open('Case1compcij', 'rb') as fp:
    compcijlist = pickle.load(fp)

with open('Case1compmij', 'rb') as fp:
    compmijlist = pickle.load(fp)



In [ ]:
DPslist = compDPslist[15][0:3]
cijlist = compcijlist[15][0:3]
Fijlist = compFijlist[15][0:3]
mijlist = compmijlist[15][0:3]
period = 0

## Extract Additional Parameters

In [3]:
def runmodelA(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, Pi, solutionnumber, Tcost, period):
    DPs = DPslist[solutionnumber]
    LDC = DPs.copy()
    Si = DPs.loc[:,'Supply']
    Dj = DPs.loc[:,'ActualDemand']
    Fij = Fijlist[solutionnumber]
    cij = cijlist[solutionnumber]
    mij = mijlist[solutionnumber]

    m = Model()

    # Add variables


    yhi = {} #flow of goods between supply nodes
    xii = {} #binary value equal to 1 if supply node i is to be opened for pre-positioning
    yij = {} #flow of goods from supply node i to demand node j
    xij = {} #Binary variable equal to 1 if demand node j is allocated to supply node i
    Fi = {} #maximum prepositioning time at supply node i

    #define yhi as integer
    for h in range(len(LDC)):
        for i in range(len(LDC)):
            yhi[(h,i)] = m.addVar(lb=0, vtype=GRB.INTEGER)

    #define xii as binary
    for i in range(len(LDC)):
        xii[i] = m.addVar(vtype=GRB.BINARY)

    #define yij as integer
    for i in range(len(LDC)):
          for j in range(len(DPs)):
                yij[(i,j)] = m.addVar(lb=0, vtype=GRB.INTEGER)

    #define xij as binary
    for i in range(len(LDC)):
          for j in range(len(DPs)):
                xij[(i,j)] = m.addVar(lb=0, vtype=GRB.BINARY)

    #define Fi as integer 
    for i in range(len(LDC)):
        Fi[i] = m.addVar(lb=0, vtype=GRB.INTEGER)

    m.update()

#     4 Ensures that the total number of supply nodes is maximum of p
#     m.addConstr(quicksum(xii[i] for i in range(len(LDC))) <= p)

    #5 ensures flow at node j from all supply nodes is not greater than amount demanded at j
    for j in range(len(DPs)):
        m.addConstr(quicksum(yij[(i,j)] for i in range(len(LDC))) <= Dj[j])

    #6 j is only assigned to i if goods can be delivered from i to j withink K hours
    for i in range(len(LDC)):
        for j in range(len(DPs)):
            m.addConstr(xij[(i,j)] <= xii[i])

    # ensures that if i is assigned to j, that the maximum pre-positioning time at i takes into account the amount of time before the typhoon reaches j
    for i in range(len(LDC)):
        for j in range(len(DPs)):
                m.addConstr(Fi[i] <= (1-xij[(i,j)])*Fij.iloc[i,i] + xij[(i,j)]*Fij.iloc[i,j])

    #7 Ensures that goods can only be prepositioned at i if the time needed for pre-position does not exceed the maximum pre-positioning time allowed at i
    for h in range(len(LDC)):
          for i in range(len(LDC)):
                m.addConstr(mhi.iloc[h,i]*xii[i] +
                            (1-xiiinit.iloc[i,0])*xii[i]*uio 
                            <= 
                            Fi[i]
                           )


    #8 Ensures that there is enough quantity of supply at node i to deliver to node j
    for i in range(len(LDC)):
        m.addConstr(quicksum(yij[(i,j)] for j in range(len(DPs))) 
                    <=
                    Qi.iloc[i,0] 
                    +
                    quicksum(yhi[(h,i)] for h in range(len(LDC))) 
                    -
                    quicksum(yhi[(i,h)] for h in range(len(LDC))) 
                    )

    #9 Ensures that the quantity of goods delivered from LDC i to DPs does not exceed the capacity of the LDC
    for i in range(len(LDC)):
        m.addConstr(xii[i]*capi.iloc[i,0]                
                            >= quicksum(yij[(i,j)] for j in range(len(DPs))))

    #10 Ensures that DP j is served only if j is allocated to i
    for i in range(len(LDC)):
        for j in range(len(DPs)):
            m.addConstr(yij[(i,j)] <= 1000000 * xij[(i,j)])

#     #11 Ensures the path is selected for delivery from LDC to DPs is available based on the forecast
#     for i in range(len(LDC)):
#         for j in range(len(DPs)):
#             m.addConstr(xij[(i,j)] <= Rij.iloc[i,j])

    #12 Ensures that supply node h has the quantity needed to deliver to supply node i
    for i in range(len(LDC)):
        m.addConstr(quicksum(yhi[(i,h)] for h in range(len(LDC))) <= Qi.iloc[i,0])
    
    #Ensures that no supply goods are pre-positioned to permanently placed goods
    for h in range(len(LDC)):
        for i in range(len(LDC)):
            m.addConstr(yhi[(i,h)] <= 1000000*(1-Pi.iloc[i,0])*(1-Pi.iloc[h,0]))

    #Ensures that no supply is prepositioned to a node that is potentially destroyed
    for i in range(len(LDC)):
        m.addConstr(quicksum(yhi[(h,i)] for h in range(len(LDC))) <= 1000000*(Si[i]))  
    
    #11 Ensures the path is selected for delivery from LDC to DPs is available based on the forecast
    for i in range(len(LDC)):
        for j in range(len(DPs)):
            m.addConstr(xij[(i,j)] <= (Si[i]))
    
#     #Ensures that the used budget is less than B
#     m.addConstr(quicksum(quicksum(
#                     chi.iloc[h,i]*yhi[(h,i)]
#                     for i in range(len(LDC))) for h in range(len(LDC))) 
#                     +
#                     quicksum(
#                     (1-xiiinit.iloc[i,0])*xii[i]*cio 
# #                         + 
# #                     xiiinit.iloc[i,0]*(1-xii[i])*cic
#                     for i in range(len(LDC)))
#                     +
#                     quicksum(quicksum(
#                     cij.iloc[i,j]*yij[(i,j)]
#                     for i in range(len(LDC))) for j in range(len(LDC))) + Tcost <= B)
        
    m.setParam("MIPGap", 1e-8)
    m.setParam("TimeLimit", 5.0)
    m.setParam("NodefileStart", 0.05)
    # #Set Objective Functions
    # Objective Function 1 Min Costs
    m.setObjectiveN(quicksum(quicksum(
                    chi.iloc[h,i]*yhi[(h,i)]
                    for i in range(len(LDC))) for h in range(len(LDC))) 
                    +
                    quicksum(
                    (1-xiiinit.iloc[i,0])*xii[i]*cio 
#                         + 
#                     xiiinit.iloc[i,0]*(1-xii[i])*cic
                    for i in range(len(LDC)))
                    +
                    quicksum(quicksum(
                    cij.iloc[i,j]*yij[(i,j)]
                    for i in range(len(LDC))) for j in range(len(LDC)))
                    , 
                    index=1, priority=1, weight=1 )

    #Objective Function 2 Min Supply Destroyed
    m.setObjectiveN(quicksum(quicksum(yij[(i,j)]*(mij.iloc[i,j])
                    for i in range(len(LDC))) for j in range(len(DPs))), 
                    index=2, priority=2, weight=1 )

    #Objective Function 3 Max Demand Supplied
    m.setObjectiveN(quicksum(quicksum(yij[(i,j)] 
                    for i in range(len(LDC))) for j in range(len(DPs))), 
                    index=3, priority=3, weight=-1)


    m.optimize()

    variablelist = m.getVars()
    variablelist = [i.x for i in variablelist]

    yhi = pd.DataFrame(np.array(variablelist[:len(DPs)**2]).reshape(len(DPs),len(DPs)))
    xii = pd.DataFrame(variablelist[len(DPs)**2:len(DPs)**2+len(DPs)])
    yij = pd.DataFrame(np.array(variablelist[len(DPs)**2+len(DPs):len(DPs)**2+len(DPs)+len(DPs)**2]).reshape(len(DPs),len(DPs)))
    xij = pd.DataFrame(np.array(variablelist[len(DPs)**2+len(DPs)+len(DPs)**2:len(DPs)**2+len(DPs)+len(DPs)**2+len(DPs)**2]).reshape(len(DPs),len(DPs)))
    Fi = pd.DataFrame(variablelist[len(DPs)**2+len(DPs)+len(DPs)**2+len(DPs)**2:])

    pd.set_option('display.max_columns', None)  
    yhi2 = yhi[(yhi.T != 0).any()]
    xii2 = xii[(xii.T != 0).any()]
    yij2 = yij[(yij.T != 0).any()]
    xij2 = xij[(xij.T != 0).any()]
    Fi2 = Fi[(Fi.T != 0).any()]
    
    costA = yij.copy()
    costB = xii.copy()
    dyij = yij.copy()
    dist = yij.copy()
    for i in range(len(dyij)):
        for j in range(len(dyij)):
            dyij.iloc[i,j] = yij.iloc[i,j]*(1-Si[i])
            costA.iloc[i,j] = chi.iloc[i,j]*yhi.iloc[i,j] + cij.iloc[i,j]*yij.iloc[i,j]
            dist.iloc[i,j] = yij.iloc[i,j]*cij.iloc[i,j]
    for i in range(len(costB)):
        costB.iloc[i,0] = (1-xiiinit.iloc[i,0])*xii.iloc[i,0]*cio
    
    Qinew = Qi.copy()
    DD = Qi.copy()
    for i in range(len(Qinew)):
        Qinew.iloc[i,0] = Qi.iloc[i,0] - yhi.sum(axis=1)[i] + yhi.sum(axis=0)[i]
        DD.iloc[i,0] = Qinew.iloc[i,0]*(1-Si[i])
    
    if yij.sum().sum() == 0:
        avedist = 0
    else:
        avedist = dist.sum().sum()/yij.sum().sum()
        
    
    listA = pd.DataFrame(np.zeros((1, 0)))
    listA['Period'] = period
    listA['Solution'] = solutionnumber
    listA['Demand'] = Dj.sum()
    listA['SuppliedDemand'] = yij.sum().sum()
    listA['DestroyedDemand'] = DD.sum().sum()
    listA['AverageDistance'] = avedist
    listA['Cost'] = Tcost + costA.sum().sum() + costB.sum()
    listA['Facilities'] = xii.sum()
    listA = pd.concat([listA, Qinew.T], axis=1)
    return listA, yhi, xii, yij, xij, Fi 

In [ ]:
yhilist = list()
xiilist = list()
yijlist = list()
xijlist = list()
Filist = list()
for solutionnumber in range(len(DPslist)):
    if solutionnumber == 0:
        ADF, yhi, xii, yij, xij, Fi = runmodelA(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, Pi, solutionnumber, Tcost, period)
    else:
        ADFnew, yhi, xii, yij, xij, Fi = runmodelA(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, Pi, solutionnumber, Tcost, period)
        ADF = ADF.append(ADFnew)
    yhilist.append(yhi)
    xiilist.append(xii)
    yijlist.append(yij)
    xijlist.append(xij)
    Filist.append(Fi)
ADF = ADF.reset_index(drop = True)

In [ ]:
ADF

In [4]:
def runmodelB(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, solutionnumber, scenarionumber, period, yhilist, Tcost):

    DPs = DPslist[scenarionumber]
    LDC = DPs.copy()
    Si = DPs.loc[:,'Supply']
    Dj = DPs.loc[:,'ActualDemand']
    Fij = Fijlist[scenarionumber]
    cij = cijlist[scenarionumber]
    mij = mijlist[scenarionumber]
    yhi = yhilist[solutionnumber]

    


    m = Model()


    # Add variables


    xii = {} #binary value equal to 1 if supply node i is to be opened for pre-positioning
    yij = {} #flow of goods from supply node i to demand node j
    xij = {} #Binary variable equal to 1 if demand node j is allocated to supply node i
    Fi = {} #maximum prepositioning time at supply node i

    #define xii as binary
    for i in range(len(LDC)):
        xii[i] = m.addVar(vtype=GRB.BINARY)

    #define yij as integer
    for i in range(len(LDC)):
          for j in range(len(DPs)):
                yij[(i,j)] = m.addVar(lb=0, vtype=GRB.INTEGER)

    #define xij as binary
    for i in range(len(LDC)):
          for j in range(len(DPs)):
                xij[(i,j)] = m.addVar(lb=0, vtype=GRB.BINARY)

    #define Fi as integer 
    for i in range(len(LDC)):
        Fi[i] = m.addVar(lb=0, vtype=GRB.INTEGER)

    m.update()


    #5 ensures flow at node j from all supply nodes is not greater than amount demanded at j
    for j in range(len(DPs)):
        m.addConstr(quicksum(yij[(i,j)] for i in range(len(LDC))) <= Dj[j])

    #6 j is only assigned to i if goods can be delivered from i to j withink K hours
    for i in range(len(LDC)):
        for j in range(len(DPs)):
            m.addConstr(xij[(i,j)] <= xii[i])

    # ensures that if i is assigned to j, that the maximum pre-positioning time at i takes into account the amount of time before the typhoon reaches j
    for i in range(len(LDC)):
        for j in range(len(DPs)):
                m.addConstr(Fi[i] <= (1-xij[(i,j)])*Fij.iloc[i,i] + xij[(i,j)]*Fij.iloc[i,j])

    #7 Ensures that goods can only be prepositioned at i if the time needed for pre-position does not exceed the maximum pre-positioning time allowed at i
    for h in range(len(LDC)):
          for i in range(len(LDC)):
                m.addConstr( 
                            mhi.iloc[h,i]*xii[i] +
                            (1-xiiinit.iloc[i,0])*xii[i]*uio 
                            <= 
                            Fi[i]
                           )


    #8 Ensures that there is enough quantity of supply at node i to deliver to node j
    for i in range(len(LDC)):
        m.addConstr(quicksum(yij[(i,j)] for j in range(len(DPs))) 
                    <=
                    Qi.iloc[i,0] - yhi.sum(axis=1)[i] + yhi.sum(axis=0)[i]
                    )

    #9 Ensures that the quantity of goods delivered from LDC i to DPs does not exceed the capacity of the LDC
    for i in range(len(LDC)):
        m.addConstr(xii[i]*capi.iloc[i,0]                
                            >= quicksum(yij[(i,j)] for j in range(len(DPs))))

    #10 Ensures that DP j is served only if j is allocated to i
    for i in range(len(LDC)):
        for j in range(len(DPs)):
            m.addConstr(yij[(i,j)] <= 1000000 * xij[(i,j)])

    #11 Ensures the path is selected for delivery from LDC to DPs is available based on the forecast
    for i in range(len(LDC)):
        for j in range(len(DPs)):
            m.addConstr(xij[(i,j)] <= (Si[i]))
    

    m.setParam("MIPGap", 1e-8)
    m.setParam("TimeLimit", 5.0)
    m.setParam("NodefileStart", 0.05)
    # #Set Objective Functions
#     Objective Funciton 1 Min Costs
    m.setObjectiveN(quicksum(quicksum(
                    chi.iloc[h,i]*yhi.iloc[h,i]
                    for i in range(len(LDC))) for h in range(len(LDC))) 
                    +
                    quicksum(
                    (1-xiiinit.iloc[i,0])*xii[i]*cio 
                    for i in range(len(LDC)))
                    +
                    quicksum(quicksum(
                    cij.iloc[i,j]*yij[(i,j)]
                    for i in range(len(LDC))) for j in range(len(LDC)))
                    , 
                    index=1, priority=1, weight=1 )

    #Objective Function 2 Min Supply Destroyed
    m.setObjectiveN(quicksum(quicksum(yij[(i,j)]*(mij.iloc[i,j])
                    for i in range(len(LDC))) for j in range(len(DPs))), 
                    index=2, priority=2, weight=1 )

    #Objective Function 3 Max Demand Supplied
    m.setObjectiveN(quicksum(quicksum(yij[(i,j)] 
                    for i in range(len(LDC))) for j in range(len(DPs))), 
                    index=3, priority=3, weight=-1)



    m.optimize()

    variablelist = m.getVars()
    variablelist = [i.x for i in variablelist]

    xii = pd.DataFrame(variablelist[:len(DPs)])
    yij = pd.DataFrame(np.array(variablelist[len(DPs):len(DPs)+len(DPs)**2]).reshape(len(DPs),len(DPs)))
    xij = pd.DataFrame(np.array(variablelist[len(DPs)+len(DPs)**2:+len(DPs)+len(DPs)**2+len(DPs)**2]).reshape(len(DPs),len(DPs)))
    Fi = pd.DataFrame(variablelist[len(DPs)+len(DPs)**2+len(DPs)**2:])

    pd.set_option('display.max_columns', None)  
    yhi2 = yhi[(yhi.T != 0).any()]
    xii2 = xii[(xii.T != 0).any()]
    yij2 = yij[(yij.T != 0).any()]
    xij2 = xij[(xij.T != 0).any()]
    Fi2 = Fi[(Fi.T != 0).any()]

    costA = yij.copy()
    costB = xii.copy()
    dyhi = Si.copy()
    dist = yij.copy()
    for i in range(len(LDC)):
        for j in range(len(DPs)):
            #costA is the cost of transferring between supply nodes (h to i) and from supply nodes to demand nodes (i to j)
            costA.iloc[i,j] = chi.iloc[i,j]*yhi.iloc[i,j] + cij.iloc[i,j]*yij.iloc[i,j]
            dist.iloc[i,j] = yij.iloc[i,j]*cij.iloc[i,j]
    for i in range(len(LDC)):
        #costB is the cost of setup (and closure) and opened and closed nodeds
        costB.iloc[i,0] = (1-xiiinit.iloc[i,0])*xii.iloc[i,0]*cio 
#         + xiiinit.iloc[i,0]*(1-xii.iloc[i,0])*cic
        dyhi[i] = (1-Si[i])*yhi.sum(axis=0)[i]

    Qinew = Qi.copy()
    DD = Qi.copy()
    for i in range(len(Qinew)):
        Qinew.iloc[i,0] = Qi.iloc[i,0] - yhi.sum(axis=1)[i] + yhi.sum(axis=0)[i]
        DD.iloc[i,0] = Qinew.iloc[i,0]*(1-Si[i])
    
    
    if yij.sum().sum() == 0:
        avedist = 0
    else:
        avedist = dist.sum().sum()/yij.sum().sum()
       

    listA = pd.DataFrame(np.zeros((1, 0)))
    listA['Period'] = period
    listA['Scenario'] = scenarionumber
    listA['Solution'] = solutionnumber
    listA['Demand'] = Dj.sum()
    listA['SuppliedDemand'] = yij.sum().sum()
    listA['DestroyedDemand'] = DD.sum().sum()
    listA['AverageDistance'] = avedist
    listA['Cost'] = Tcost + costA.sum().sum() + costB.sum()
    listA['Facilities'] = xii.sum()
#     listA = pd.concat([listA, Qinew.T], axis=1)
    
    return listA

In [ ]:
for scenarionumber in range(len(DPslist)):
    for solutionnumber in range(len(DPslist)):
        if solutionnumber == 0 and scenarionumber == 0:
            BDF = runmodelB(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, solutionnumber, scenarionumber, period, yhilist, Tcost)
        else:
            BDF = BDF.append(runmodelB(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, solutionnumber, scenarionumber, period, yhilist, Tcost))

In [ ]:
BDF = BDF.reset_index(drop=True)
BDF

In [ ]:
maxSD = list()
mindist = list()
minC = list()

BDF2 = BDF.copy()
for i in range(len(BDF2)):
    if BDF2.loc[i,'Scenario'] == BDF2.loc[i,'Solution']:
        maxSD.append(BDF2.loc[i,'SuppliedDemand'])
        mindist.append(BDF2.loc[i,'AverageDistance'])
        minC.append(BDF2.loc[i,'Cost'])
    
for i in range(len(BDF2)):
    BDF2.loc[i,'SDabs'] = round(BDF2.loc[i,'SuppliedDemand']/BDF2.loc[i,'Demand']*100,2)
#     BDF2.loc[i,'DDabs'] = round(BDF2.loc[i,'DestroyedDemand']/BDF2.loc[i,'Demand']*100,2)
    BDF2.loc[i,'Dstabs'] = BDF2.loc[i,'AverageDistance']
    BDF2.loc[i,'Cabs'] = round(BDF2.loc[i,'Cost'],2)
    BDF2.loc[i, 'SDrel'] = round((maxSD[int(BDF2.loc[i,'Scenario'])] - BDF2.loc[i,'SuppliedDemand'])/ maxSD[int(BDF2.loc[i,'Scenario'])] *100,2)
#     BDF2.loc[i, 'DDrel'] = round((maxSD[int(BDF2.loc[i,'Scenario'])] - BDF2.loc[i,'DestroyedDemand'] )/maxSD[int(BDF2.loc[i,'Scenario'])]*100,2)
    BDF2.loc[i, 'Dstrel'] = round((BDF2.loc[i,'AverageDistance'] - mindist[int(BDF2.loc[i,'Scenario'])] ),2)
    BDF2.loc[i, 'Crel'] = BDF2.loc[i,'Cost'] - minC[int(BDF2.loc[i,'Scenario'])]
    
    
BDFmean = BDF2.groupby(['Solution']).mean()
BDFmax = BDF2.groupby(['Solution']).max()
# BDFmin = BDF3 = BDF2.groupby(['Solution']).min()
BDF2 = pd.concat([BDFmean.iloc[:,:11], BDFmax.iloc[:,11:]], axis=1)
abskey = None
relkey = None

abskeytent = np.argwhere(BDF2.SDabs.tolist() == np.amax(BDF2.SDabs.tolist())).flatten().tolist()
if len(abskeytent) > 1:
    BDF2new = BDF2.loc[abskeytent,:]
    newabskeytent = np.argwhere(BDF2new.Dstabs.tolist() == np.amin(BDF2new.Dstabs.tolist())).flatten().tolist()
    abskeytent = [abskeytent[i] for i in newabskeytent] 
    if len(abskeytent) > 1:
        BDF2new = BDF2.loc[abskeytent,:]
        newabskeytent = np.argwhere(BDF2new.Cabs.tolist() == np.amin(BDF2new.Cabs.tolist())).flatten().tolist()
        abskeytent = [abskeytent[i] for i in newabskeytent] 
abskey = abskeytent[0]


relkeytent = np.argwhere(BDF2.SDrel.tolist() == np.amin(BDF2.SDrel.tolist())).flatten().tolist()
if len(relkeytent) > 1:
    BDF2new = BDF2.loc[relkeytent,:]
    newrelkeytent = np.argwhere(BDF2new.Dstrel.tolist() == np.amin(BDF2new.Dstrel.tolist())).flatten().tolist()
    relkeytent = [relkeytent[i] for i in newrelkeytent ] 
    if len(relkeytent) > 1:
        print(relkeytent)
        BDF2new = BDF2.loc[relkeytent,:]
        newrelkeytent = np.argwhere(BDF2new.Crel.tolist() == np.amin(BDF2new.Crel.tolist())).flatten().tolist()
        relkeytent = [relkeytent[i] for i in newrelkeytent ]
relkey = relkeytent[0]

keycode = 'abs'
    

In [ ]:
abskey

In [ ]:
relkey

In [ ]:
if keycode == 'abs':
    key = abskey
elif keycode == 'rel':
    key = relkey

In [ ]:
minFij = Fijlist[0]*0+500
for i in range(len(Fijlist)):
    for j in range(len(Fijlist[0])):
        for k in range(len(Fijlist[0])):
            minFij.iloc[j,k] = min(Fijlist[i].iloc[j,k],minFij.iloc[j,k])

In [ ]:
#Strategy 1 - pre-position at the last minute

xijnew = xijlist[abskey]
xijnew = xijnew.replace({0:np.nan})
minprep = xijnew*minFij
minprep = minprep.min(axis=1)
minprep = minprep.to_frame()

mhinew = mhi.reset_index(drop=True)
mhinew.columns = range(mhinew.shape[1])
mhinew = mhinew*(yhilist[abskey]/yhilist[abskey])
mhinew = mhinew.max(axis=0).to_frame()
mhinew = mhinew.replace({np.nan:0})

preptime = (1-xiiinit)*xiilist[abskey]*uio + mhinew
extratime = minprep - preptime

for i in range(len(extratime)):
    if extratime.iloc[i,0] < 6:
        Pi.iloc[i,0] = 1

In [ ]:
yhicopy = yhilist[abskey].copy()
for i in range(len(yhilist[abskey])):
    for j in range(len(yhilist[abskey])):
        yhicopy.iloc[i,j] = yhicopy.iloc[i,j]*Pi.iloc[j,0]

for i in range(len(Qi)):
    Qi.iloc[i,0] = Qi.iloc[i,0] - yhicopy.sum(axis=1)[i] + yhicopy.sum(axis=0)[i]

In [ ]:
Tcost1 = yhicopy.copy()
Tcost2 = xiilist[key].copy()
for i in range(len(yhicopy)):
    for j in range(len(yhicopy)):
        Tcost1.iloc[i,j] = chi.iloc[i,j]*yhicopy.iloc[i,j] 
for i in range(len(xiilist[key])):
    Tcost2.iloc[i,0] = (1-xiiinit.iloc[i,0])*(Qi/Qi).iloc[i,0]*cio 

Tcost = Tcost + Tcost1.sum().sum() + Tcost2.sum().sum()
xiiinit = (Qi/Qi).replace({np.nan:0})
Pi.equals(xiilist[key])

In [ ]:
xiilist[key]

In [7]:
start_time = time.time()

ADFlist = list()
BDFlist = list()
BDF2list = list()
keylist = list()
Qilist = list()
Tcostlist = list()
xiiinitlist = list()
Pilist = list()
yijmasterlist = list()
yhimasterlist = list()
extratimelist = list()
preptimelist = list()

for period in range(len(compDPslist)):
    print('period %d' % period)
#     Qilist.append(Qi)
#     Pilist.append(Pi)
    print(Pi)
    print(Qi)
    if len(compDPslist[period])>1:
        DPslist = compDPslist[period]
        cijlist = compcijlist[period]
        Fijlist = compFijlist[period]
        mijlist = compmijlist[period]

        #RUN MODEL A
        yhilist = list()
        xiilist = list()
        yijlist = list()
        xijlist = list()
        Filist = list()
        for solutionnumber in range(len(DPslist)):
            if solutionnumber == 0:
                ADF, yhi, xii, yij, xij, Fi = runmodelA(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, Pi, solutionnumber, Tcost, period)
            else:
                ADFnew, yhi, xii, yij, xij, Fi = runmodelA(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, Pi, solutionnumber, Tcost, period)
                ADF = ADF.append(ADFnew)
            yhilist.append(yhi)
            xiilist.append(xii)
            yijlist.append(yij)
            xijlist.append(xij)
            Filist.append(Fi)
        ADF = ADF.reset_index(drop = True)
        
        ADFlist.append(ADF)
        
        
        #RUN MODEL B
        for scenarionumber in range(len(DPslist)):
            for solutionnumber in range(len(DPslist)):
                if solutionnumber == 0 and scenarionumber == 0:
                    BDF = runmodelB(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, solutionnumber, scenarionumber, period, yhilist, Tcost)
                else:
                    BDF = BDF.append(runmodelB(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, solutionnumber, scenarionumber, period, yhilist, Tcost))

        BDF = BDF.reset_index(drop=True)
        BDFlist.append(BDF)
        
        
        #COMPUTE FOR BDF2 TO DETERMINE THE ROBUST SOLUTION
        maxSD = list()
        mindist = list()
        minC = list()

        BDF2 = BDF.copy()
        for i in range(len(BDF2)):
            if BDF2.loc[i,'Scenario'] == BDF2.loc[i,'Solution']:
                maxSD.append(BDF2.loc[i,'SuppliedDemand'])
                mindist.append(BDF2.loc[i,'AverageDistance'])
                minC.append(BDF2.loc[i,'Cost'])

        for i in range(len(BDF2)):
            BDF2.loc[i,'SDabs'] = round(BDF2.loc[i,'SuppliedDemand']/BDF2.loc[i,'Demand']*100,2)
        #     BDF2.loc[i,'DDabs'] = round(BDF2.loc[i,'DestroyedDemand']/BDF2.loc[i,'Demand']*100,2)
            BDF2.loc[i,'Dstabs'] = BDF2.loc[i,'AverageDistance']
            BDF2.loc[i,'Cabs'] = round(BDF2.loc[i,'Cost'],2)
            BDF2.loc[i, 'SDrel'] = round((maxSD[int(BDF2.loc[i,'Scenario'])] - BDF2.loc[i,'SuppliedDemand'])/ maxSD[int(BDF2.loc[i,'Scenario'])] *100,2)
        #     BDF2.loc[i, 'DDrel'] = round((maxSD[int(BDF2.loc[i,'Scenario'])] - BDF2.loc[i,'DestroyedDemand'] )/maxSD[int(BDF2.loc[i,'Scenario'])]*100,2)
            BDF2.loc[i, 'Dstrel'] = round((BDF2.loc[i,'AverageDistance'] - mindist[int(BDF2.loc[i,'Scenario'])] ),2)
            BDF2.loc[i, 'Crel'] = BDF2.loc[i,'Cost'] - minC[int(BDF2.loc[i,'Scenario'])]


        BDFmean = BDF2.groupby(['Solution']).mean()
        BDFmax = BDF2.groupby(['Solution']).max()
        # BDFmin = BDF3 = BDF2.groupby(['Solution']).min()
        BDF2 = pd.concat([BDFmean.iloc[:,:11], BDFmax.iloc[:,11:]], axis=1)
        abskey = None
        relkey = None
        
        BDF2list.append(BDF2)

        abskeytent = np.argwhere(BDF2.SDabs.tolist() == np.amax(BDF2.SDabs.tolist())).flatten().tolist()
        if len(abskeytent) > 1:
            BDF2new = BDF2.loc[abskeytent,:]
            newabskeytent = np.argwhere(BDF2new.Dstabs.tolist() == np.amin(BDF2new.Dstabs.tolist())).flatten().tolist()
            abskeytent = [abskeytent[i] for i in newabskeytent] 
            if len(abskeytent) > 1:
                BDF2new = BDF2.loc[abskeytent,:]
                newabskeytent = np.argwhere(BDF2new.Cabs.tolist() == np.amin(BDF2new.Cabs.tolist())).flatten().tolist()
                abskeytent = [abskeytent[i] for i in newabskeytent] 
        abskey = abskeytent[0]


        relkeytent = np.argwhere(BDF2.SDrel.tolist() == np.amin(BDF2.SDrel.tolist())).flatten().tolist()
        if len(relkeytent) > 1:
            BDF2new = BDF2.loc[relkeytent,:]
            newrelkeytent = np.argwhere(BDF2new.Dstrel.tolist() == np.amin(BDF2new.Dstrel.tolist())).flatten().tolist()
            relkeytent = [relkeytent[i] for i in newrelkeytent ] 
            if len(relkeytent) > 1:
                print(relkeytent)
                BDF2new = BDF2.loc[relkeytent,:]
                newrelkeytent = np.argwhere(BDF2new.Crel.tolist() == np.amin(BDF2new.Crel.tolist())).flatten().tolist()
                relkeytent = [relkeytent[i] for i in newrelkeytent ]
        relkey = relkeytent[0]
        
        #SPECIFY ROBUSTNESS CRITERIA
        keycode = 'rel'
        
        if keycode == 'abs':
            key = abskey
        elif keycode == 'rel':
            key = relkey
        
        keylist.append(key)
        
        #DETERMINE MINIMUM PREP TIME
        minFij = Fijlist[0]*0+500
        for i in range(len(Fijlist)):
            for j in range(len(Fijlist[0])):
                for k in range(len(Fijlist[0])):
                    minFij.iloc[j,k] = min(Fijlist[i].iloc[j,k],minFij.iloc[j,k])
        
        
        #Strategy 1 - pre-position at the last minute
        xijnew = xijlist[key]
        xijnew = xijnew.replace({0:np.nan})
        minprep = xijnew*minFij
        minprep = minprep.min(axis=1)
        minprep = minprep.to_frame()

        mhinew = mhi.reset_index(drop=True)
        mhinew.columns = range(mhinew.shape[1])
        mhinew = mhinew*(yhilist[key]/yhilist[key])
        mhinew = mhinew.max(axis=0).to_frame()
        mhinew = mhinew.replace({np.nan:0})

        preptime = (1-xiiinit)*xiilist[key]*uio + mhinew
        extratime = minprep - preptime

        for i in range(len(extratime)):
            if extratime.iloc[i,0] < 6:
                Pi.iloc[i,0] = 1

        yhicopy = yhilist[key].copy()
        for i in range(len(yhilist[key])):
            for j in range(len(yhilist[key])):
                yhicopy.iloc[i,j] = yhicopy.iloc[i,j]*Pi.iloc[j,0]

        for i in range(len(Qi)):
            Qi.iloc[i,0] = Qi.iloc[i,0] - yhicopy.sum(axis=1)[i] + yhicopy.sum(axis=0)[i]

        Tcost1 = yhicopy.copy()
        Tcost2 = xiilist[key].copy()
        for i in range(len(yhicopy)):
            for j in range(len(yhicopy)):
                Tcost1.iloc[i,j] = chi.iloc[i,j]*yhicopy.iloc[i,j] 
        for i in range(len(xiilist[key])):
            Tcost2.iloc[i,0] = (1-xiiinit.iloc[i,0])*(Qi/Qi).iloc[i,0]*cio 

        Tcost = Tcost + Tcost1.sum().sum() + Tcost2.sum().sum()
        xiiinit = (Qi/Qi).replace({np.nan:0})
        
        print(Pi.equals(xiilist[key]))
        Qi2 = Qi.copy()
        Pi2 = Pi.copy()
        Qilist.append(Qi2)
        Pilist.append(Pi2)
        
#         Qilist.append(Qi)
        Tcostlist.append(Tcost)
        xiiinitlist.append(xiiinit)
#         Pilist.append(Pi)
        yijmasterlist.append(yijlist[key])
        yhimasterlist.append(yhilist[key])
        extratimelist.append(extratime)
        preptimelist.append(preptime)
        
        Pifake = Pi.copy()
        Pifake.iloc[20,0] = 1
        
#         if Pifake.equals(xiilist[key]):
#             break
        
        
print("--- %s seconds ---" % (time.time() - start_time))      

    
    
    

period 0
      0
0   0.0
1   0.0
2   0.0
3   0.0
4   0.0
5   0.0
6   0.0
7   0.0
8   0.0
9   0.0
10  0.0
11  0.0
12  0.0
13  0.0
14  0.0
15  0.0
16  0.0
17  0.0
18  0.0
19  0.0
20  0.0
21  0.0
22  0.0
23  0.0
24  0.0
25  0.0
26  0.0
27  0.0
28  0.0
29  0.0
30  0.0
31  0.0
32  0.0
33  0.0
34  0.0
35  0.0
36  0.0
37  0.0
38  0.0
39  0.0
40  0.0
41  0.0
42  0.0
43  0.0
          0
0       0.0
1       0.0
2       0.0
3       0.0
4       0.0
5       0.0
6       0.0
7       0.0
8       0.0
9       0.0
10      0.0
11      0.0
12      0.0
13      0.0
14      0.0
15      0.0
16      0.0
17      0.0
18      0.0
19      0.0
20  30000.0
21      0.0
22      0.0
23      0.0
24      0.0
25      0.0
26      0.0
27      0.0
28      0.0
29      0.0
30      0.0
31      0.0
32      0.0
33      0.0
34      0.0
35      0.0
36      0.0
37      0.0
38      0.0
39      0.0
40      0.0
41      0.0
42      0.0
43      0.0
period 1
      0
0   0.0
1   0.0
2   0.0
3   0.0
4   0.0
5   0.0
6   0.0
7   0.0
8   0.0
9 

   Prev: 0.0001  Min: 0.0  Max: 1e+100  Default: 0.0001
Changed value of parameter TimeLimit to 5.0
   Prev: 1e+100  Min: 0.0  Max: 1e+100  Default: 1e+100
Changed value of parameter NodefileStart to 0.05
   Prev: 1e+100  Min: 0.0  Max: 1e+100  Default: 1e+100
Optimize a model with 11836 rows, 5896 columns and 31535 nonzeros
Variable types: 0 continuous, 5896 integer (1980 binary)
Coefficient statistics:
  Matrix range     [1e-01, 1e+06]
  Objective range  [2e-02, 3e+04]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 1e+06]

---------------------------------------------------------------------------
Multi-objectives: starting optimization with 4 objectives ... 
---------------------------------------------------------------------------

Multi-objectives: applying initial presolve ...
---------------------------------------------------------------------------

Presolve removed 8513 rows and 3195 columns
Presolve time: 0.05s
Presolved: 3323 rows and 2701 columns
-----------

Solution count 2: 0 40786 

Optimal solution found (tolerance 1.00e-08)
Best objective 0.000000000000e+00, best bound 0.000000000000e+00, gap 0.0000%
---------------------------------------------------------------------------

Multi-objectives: optimize objective 3 () ...
---------------------------------------------------------------------------


Loaded MIP start with objective 1.36524e+06

Presolve removed 2919 rows and 2390 columns
Presolve time: 0.00s
Presolved: 8 rows, 16 columns, 23 nonzeros
Found heuristic solution: objective 431163.02439
Variable types: 0 continuous, 16 integer (9 binary)

Root relaxation: objective 3.656558e+05, 10 iterations, 0.00 seconds

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0 365655.828    0    1 431163.024 365655.828  15.2%     -    0s
H    0     0                    366580.55327 365655.828  0.25%     -    0s
     0     0     cutoff

---------------------------------------------------------------------------


Loaded MIP start with objective 23068

Presolve removed 2502 rows and 1804 columns
Presolve time: 0.00s
Presolved: 29 rows, 132 columns, 396 nonzeros
Variable types: 0 continuous, 132 integer (0 binary)

Root relaxation: objective 1.377967e+02, 9 iterations, 0.00 seconds

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

*    0     0               0     137.7966667  137.79667  0.00%     -    0s

Explored 0 nodes (9 simplex iterations) in 0.14 seconds
Thread count was 4 (of 4 available processors)

Solution count 2: 137.797 23068 

Optimal solution found (tolerance 1.00e-08)
Best objective 1.377966666667e+02, best bound 1.377966666667e+02, gap 0.0000%
---------------------------------------------------------------------------

Multi-objectives: optimize objective 3 () ...
---------------------------------------

Presolve removed 2343 rows and 1760 columns
Presolve time: 0.00s
Presolved: 23 rows, 112 columns, 224 nonzeros
Variable types: 0 continuous, 112 integer (0 binary)

Root relaxation: objective -3.000000e+04, 47 iterations, 0.00 seconds

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

*    0     0               0    -30000.00000 -30000.000  0.00%     -    0s

Explored 0 nodes (47 simplex iterations) in 0.10 seconds
Thread count was 4 (of 4 available processors)

Solution count 2: -30000 0 

Optimal solution found (tolerance 1.00e-08)
Best objective -3.000000000000e+04, best bound -3.000000000000e+04, gap 0.0000%
---------------------------------------------------------------------------

Multi-objectives: optimize objective 2 () ...
---------------------------------------------------------------------------


Loaded MIP start with objective 32243.4

Presolve removed 2343 rows and 1760 c

...

Multi-objectives: solved in 0.16 seconds, solution count 3

Changed value of parameter MIPGap to 1e-08
   Prev: 0.0001  Min: 0.0  Max: 1e+100  Default: 0.0001
Changed value of parameter TimeLimit to 5.0
   Prev: 1e+100  Min: 0.0  Max: 1e+100  Default: 1e+100
Changed value of parameter NodefileStart to 0.05
   Prev: 1e+100  Min: 0.0  Max: 1e+100  Default: 1e+100
Optimize a model with 9812 rows, 3960 columns and 21462 nonzeros
Variable types: 0 continuous, 3960 integer (1980 binary)
Coefficient statistics:
  Matrix range     [1e-01, 1e+06]
  Objective range  [2e-02, 3e+04]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 3e+04]

---------------------------------------------------------------------------
Multi-objectives: starting optimization with 4 objectives ... 
---------------------------------------------------------------------------

Multi-objectives: applying initial presolve ...
---------------------------------------------------------------------------

Presolve rem

  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 3e+04]

---------------------------------------------------------------------------
Multi-objectives: starting optimization with 4 objectives ... 
---------------------------------------------------------------------------

Multi-objectives: applying initial presolve ...
---------------------------------------------------------------------------

Presolve removed 7930 rows and 2159 columns
Presolve time: 0.04s
Presolved: 1882 rows and 1801 columns
---------------------------------------------------------------------------

Multi-objectives: optimize objective 1 () ...
---------------------------------------------------------------------------

Found heuristic solution: objective 0.0000000
Presolve removed 1882 rows and 1801 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.08 seconds
Thread count was 1 (of 4 available processors)

Solution count 2: -30000 0 

Opt


Found heuristic solution: objective 0.0000000
Presolve removed 1882 rows and 1801 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.08 seconds
Thread count was 1 (of 4 available processors)

Solution count 2: -30000 0 

Optimal solution found (tolerance 1.00e-08)
Best objective -3.000000000000e+04, best bound -3.000000000000e+04, gap 0.0000%
---------------------------------------------------------------------------

Multi-objectives: optimize objective 2 () ...
---------------------------------------------------------------------------


Loaded MIP start with objective 24130.8

Presolve removed 1883 rows and 1801 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.10 seconds
Thread count was 1 (of 4 available processors)

Solution count 2: 0 24130.8 

Optimal solution found (tolerance 1.00e-08)
Best objective 0.000000000000e+00, best bound 0.000000000000e+00, 

Presolve time: 0.00s
Presolved: 37 rows, 180 columns, 530 nonzeros
Variable types: 0 continuous, 180 integer (0 binary)

Root relaxation: objective 2.293998e+03, 9 iterations, 0.00 seconds

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

*    0     0               0    2293.9983333 2293.99833  0.00%     -    0s

Explored 0 nodes (9 simplex iterations) in 0.11 seconds
Thread count was 4 (of 4 available processors)

Solution count 2: 2294 34153.3 

Optimal solution found (tolerance 1.00e-08)
Best objective 2.293998333333e+03, best bound 2.293998333333e+03, gap 0.0000%
---------------------------------------------------------------------------

Multi-objectives: optimize objective 3 () ...
---------------------------------------------------------------------------


Loaded MIP start with objective 392181

Presolve removed 1855 rows and 1753 columns
Presolve time: 0.01s
Presolved: 327 row

---------------------------------------------------------------------------


Loaded MIP start with objective 34239.4

Presolve removed 2186 rows and 1880 columns
Presolve time: 0.00s
Presolved: 38 rows, 208 columns, 613 nonzeros
Variable types: 0 continuous, 208 integer (0 binary)

Root relaxation: objective 2.198650e+03, 13 iterations, 0.00 seconds

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

*    0     0               0    2198.6500000 2198.65000  0.00%     -    0s

Explored 0 nodes (13 simplex iterations) in 0.10 seconds
Thread count was 4 (of 4 available processors)

Solution count 2: 2198.65 34239.4 

Optimal solution found (tolerance 1.00e-08)
Best objective 2.198650000000e+03, best bound 2.198650000000e+03, gap 0.0000%
---------------------------------------------------------------------------

Multi-objectives: optimize objective 3 () ...
---------------------------------

In [5]:
AA = compDPslist.copy()

for period in range(len(compDPslist)):
    for i in range(len(compDPslist[period])):
        if compDPslist[period][i].Supply.sum() == 44:
            AA[period][i] = 0
            compFijlist[period][i] = 0
            compcijlist[period][i] = 0
            compmijlist[period][i] = 0
            
AAlist = list()
BBlist = list()
CClist = list()
DDlist = list()
for period in range(len(AA)):
    A = list()
    B = list()
    C = list()
    D = list()
    for i in range(len(AA[period])):
        if isinstance(AA[period][i], pd.DataFrame):
            A.append(AA[period][i])
            B.append(compFijlist[period][i])
            C.append(compcijlist[period][i])
            D.append(compmijlist[period][i])
    AAlist.append(A)
    BBlist.append(B)
    CClist.append(C)
    DDlist.append(D)

    



In [6]:
compDPslist = AAlist.copy()[:19]
compFijlist = BBlist.copy()[:19]
compcijlist = CClist.copy()[:19]
compmijlist = DDlist.copy()[:19]

In [9]:
with open('ResultCase1REL', 'wb') as fp:
    pickle.dump(ADFlist, fp)
    pickle.dump(BDFlist, fp)
    pickle.dump(BDF2list, fp)
    pickle.dump(keylist, fp)
    pickle.dump(Qilist, fp)
    pickle.dump(Tcostlist, fp)
    pickle.dump(xiiinitlist, fp)
    pickle.dump(Pilist, fp)
    pickle.dump(yijmasterlist, fp)
    pickle.dump(yhimasterlist, fp)
    pickle.dump(extratimelist, fp)
    pickle.dump(preptimelist, fp)


In [ ]:
# with open('FINALILOILOABS', 'rb') as fp:
#     ADFlist = pickle.load(fp)
#     BDFlist = pickle.load(fp)
#     BDF2list = pickle.load(fp)
#     keylist = pickle.load(fp)
#     Qilist = pickle.load(fp)
#     Tcostlist = pickle.load(fp)
#     xiiinitlist = pickle.load(fp)
#     Pilist = pickle.load(fp)

In [10]:
Qilist

[          0
 0       0.0
 1       0.0
 2       0.0
 3    2261.0
 4       0.0
 5       0.0
 6       0.0
 7       0.0
 8       0.0
 9       0.0
 10      0.0
 11   4574.0
 12      0.0
 13      0.0
 14      0.0
 15      0.0
 16      0.0
 17      0.0
 18      0.0
 19      0.0
 20  11468.0
 21   5350.0
 22   6347.0
 23      0.0
 24      0.0
 25      0.0
 26      0.0
 27      0.0
 28      0.0
 29      0.0
 30      0.0
 31      0.0
 32      0.0
 33      0.0
 34      0.0
 35      0.0
 36      0.0
 37      0.0
 38      0.0
 39      0.0
 40      0.0
 41      0.0
 42      0.0
 43      0.0,           0
 0       0.0
 1       0.0
 2       0.0
 3    2261.0
 4       0.0
 5       0.0
 6       0.0
 7       0.0
 8       0.0
 9       0.0
 10      0.0
 11   4574.0
 12      0.0
 13      0.0
 14      0.0
 15      0.0
 16      0.0
 17      0.0
 18      0.0
 19      0.0
 20  11468.0
 21   5350.0
 22   6347.0
 23      0.0
 24      0.0
 25      0.0
 26      0.0
 27      0.0
 28      0.0
 29      0.0
 30      0.0

In [11]:
xiiinitlist

[      0
 0   0.0
 1   0.0
 2   0.0
 3   0.0
 4   0.0
 5   0.0
 6   0.0
 7   0.0
 8   0.0
 9   0.0
 10  0.0
 11  0.0
 12  0.0
 13  0.0
 14  0.0
 15  0.0
 16  0.0
 17  0.0
 18  0.0
 19  0.0
 20  1.0
 21  0.0
 22  0.0
 23  0.0
 24  0.0
 25  0.0
 26  0.0
 27  0.0
 28  0.0
 29  0.0
 30  0.0
 31  0.0
 32  0.0
 33  0.0
 34  0.0
 35  0.0
 36  0.0
 37  0.0
 38  0.0
 39  0.0
 40  0.0
 41  0.0
 42  0.0
 43  0.0,       0
 0   0.0
 1   0.0
 2   0.0
 3   0.0
 4   0.0
 5   0.0
 6   0.0
 7   0.0
 8   0.0
 9   0.0
 10  0.0
 11  0.0
 12  0.0
 13  0.0
 14  0.0
 15  0.0
 16  0.0
 17  0.0
 18  0.0
 19  0.0
 20  1.0
 21  0.0
 22  0.0
 23  0.0
 24  0.0
 25  0.0
 26  0.0
 27  0.0
 28  0.0
 29  0.0
 30  0.0
 31  0.0
 32  0.0
 33  0.0
 34  0.0
 35  0.0
 36  0.0
 37  0.0
 38  0.0
 39  0.0
 40  0.0
 41  0.0
 42  0.0
 43  0.0,       0
 0   0.0
 1   0.0
 2   0.0
 3   0.0
 4   0.0
 5   0.0
 6   0.0
 7   0.0
 8   0.0
 9   0.0
 10  0.0
 11  0.0
 12  0.0
 13  0.0
 14  0.0
 15  0.0
 16  0.0
 17  0.0
 18  0.0
 19  0.0
 

In [12]:
keylist

[0, 0, 0, 0, 1, 8, 0, 2, 2]